In [1]:
%load_ext autoreload
%autoreload 2

import torch
import torch.nn as nn
import torch.nn.functional as F
from torchvision import models
from test_config import cfg
import os
import numpy as np
import sys

np.set_printoptions(edgeitems=30, linewidth=180, 
    formatter=dict(float=lambda x: "%.3f" % x))

In [2]:
from IPython.core.display import HTML
HTML("<style>.container { width:95% !important; }</style>")

# Load model, output model arrays stage by stage whilst predicting

Using a modified version of the model file in the ./model_files folder, the model will output arrays to .npy files in the ./model_outputs folder throughout the process. I will then use these to reconstruct the step by step process to constructing the final result

In [3]:
# Generate root folder
path_lst = os.getcwd().split(os.sep)[:4]
path_lst[0] += os.sep
root_folder = os.path.join(*path_lst)

# C3 and experiment folders
c3_folder = os.path.join(root_folder, 'C-3-Framework')
exp_folder = os.path.join(c3_folder, 'exp')

# Append to sys.path
sys.path.append(c3_folder)

In [4]:
from test_classes import CvTest
from model_files.VGG16_LCM_REG import VGG16_LCM_REG

In [5]:
# Initialise
exp = '202202080823_data=london_model=VGG16_LCM_REG_lr=1e-05'

test = CvTest(
    exp=exp,
    # Overwrite default modelfile for local modified file
    net_object=VGG16_LCM_REG
)

[2022-02-25 08:20:14] === Experiment:202202080823_data=london_model=VGG16_LCM_REG_lr=1e-05 ===
[2022-02-25 08:20:14] model: VGG16_LCM_REG
[2022-02-25 08:20:14] CC: LCM
[2022-02-25 08:20:14] ===PAPER REVIEW VERSION===


In [6]:
# Generate prediction
test.pred(1)

[2022-02-25 08:20:25] x3: torch.Size([1, 512, 128, 128])
[2022-02-25 08:20:26] x4: torch.Size([1, 512, 64, 64])
[2022-02-25 08:20:26] x5: torch.Size([1, 512, 32, 32])
[2022-02-25 08:20:26] multifuse_x5: torch.Size([1, 512, 32, 32])
[2022-02-25 08:20:26] multifuse_x4: torch.Size([1, 512, 64, 64])
[2022-02-25 08:20:26] multifuse_x3: torch.Size([1, 512, 128, 128])
[2022-02-25 08:20:27] countlayer_x4_: torch.Size([1, 512, 16, 16])
[2022-02-25 08:20:27] p5: torch.Size([1, 3, 16, 16])
[2022-02-25 08:20:27] k5: torch.Size([1, 1, 16, 16])
[2022-02-25 08:20:27] i5: torch.Size([1, 3, 16, 16])
[2022-02-25 08:20:27] countlayer_x4_: torch.Size([1, 512, 16, 16])
[2022-02-25 08:20:27] p4: torch.Size([1, 3, 16, 16])
[2022-02-25 08:20:27] k4: torch.Size([1, 1, 16, 16])
[2022-02-25 08:20:27] i4: torch.Size([1, 3, 16, 16])
[2022-02-25 08:20:27] countlayer_x3_: torch.Size([1, 512, 16, 16])
[2022-02-25 08:20:27] p3: torch.Size([1, 3, 16, 16])
[2022-02-25 08:20:27] k3: torch.Size([1, 1, 16, 16])
[2022-02-25

[img_raw: (1024, 1024)]
[img: torch.Size([1, 3, 1024, 1024])]
[gt_raw: (1024, 1024)]
[gt: (1, 16, 16)]
[pred_map: (16, 16)]
[pred_map_resize: (128, 128)]

# Exploration of stages

### Load all variables

In [7]:
dct = {}

for filename in os.listdir('./model_outputs/'):
    path = os.path.join('model_outputs', filename)
    name = os.path.splitext(filename)[0]
    dct[name] = np.load(path)
    
dct

{'stage1_regress0': array([[[0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000],
         [0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000],
         [0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000],
         [0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000],
         [0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000],
         [0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000],
         [0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000],
         [0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000

## Verify result - Ok

In [8]:
(dct['stage3_regress3'] + dct['stage2_regress3'] + dct['stage1_regress3']).sum()*100

157.89848566055298

## Individual components

In [9]:
dct['stage3_regress3'], dct['stage3_regress3'].sum()

(array([[[[0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000],
          [0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000],
          [0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000],
          [0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000],
          [0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000],
          [0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000],
          [0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000],
          [0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000],
        

In [10]:
dct['stage2_regress3'], dct['stage2_regress3'].sum()

(array([[[[0.006, 0.006, 0.006, 0.007, 0.010, 0.007, 0.000, 0.000, 0.000, 0.002, 0.000, 0.000, 0.000, 0.008, 0.008, 0.007],
          [0.005, 0.004, 0.004, 0.004, 0.004, 0.004, 0.000, 0.001, 0.000, 0.000, 0.000, 0.001, 0.009, 0.004, 0.007, 0.010],
          [0.002, 0.002, 0.002, 0.004, 0.005, 0.003, 0.001, 0.000, 0.001, 0.004, 0.008, 0.008, 0.004, 0.007, 0.008, 0.005],
          [0.005, 0.003, 0.001, 0.002, 0.002, 0.006, 0.002, 0.002, 0.006, 0.003, 0.003, 0.007, 0.006, 0.004, 0.007, 0.007],
          [0.004, 0.003, 0.003, 0.003, 0.003, 0.005, 0.004, 0.007, 0.001, 0.000, 0.007, 0.006, 0.004, 0.002, 0.005, 0.005],
          [0.004, 0.005, 0.004, 0.001, 0.004, 0.004, 0.004, 0.005, 0.002, 0.006, 0.003, 0.006, 0.008, 0.005, 0.005, 0.004],
          [0.006, 0.006, 0.005, 0.006, 0.003, 0.004, 0.007, 0.003, 0.004, 0.004, 0.006, 0.008, 0.000, 0.004, 0.004, 0.005],
          [0.007, 0.004, 0.004, 0.004, 0.007, 0.006, 0.003, 0.006, 0.006, 0.002, 0.001, 0.001, 0.000, 0.001, 0.009, 0.007],
        

In [11]:
dct['stage1_regress3'], dct['stage1_regress3'].sum()

(array([[[[0.004, 0.004, 0.004, 0.004, 0.002, 0.002, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.003, 0.004],
          [0.004, 0.004, 0.005, 0.004, 0.002, 0.003, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.002, 0.002, 0.004],
          [0.004, 0.005, 0.005, 0.004, 0.001, 0.000, 0.000, 0.000, 0.000, 0.000, 0.000, 0.001, 0.001, 0.001, 0.002, 0.002],
          [0.004, 0.004, 0.005, 0.004, 0.003, 0.001, 0.000, 0.000, 0.001, 0.002, 0.004, 0.003, 0.001, 0.001, 0.003, 0.003],
          [0.004, 0.004, 0.005, 0.005, 0.002, 0.002, 0.002, 0.003, 0.003, 0.003, 0.003, 0.004, 0.004, 0.003, 0.004, 0.003],
          [0.004, 0.004, 0.004, 0.004, 0.003, 0.003, 0.002, 0.003, 0.003, 0.002, 0.003, 0.003, 0.002, 0.002, 0.004, 0.003],
          [0.003, 0.003, 0.005, 0.004, 0.005, 0.004, 0.002, 0.003, 0.003, 0.002, 0.002, 0.003, 0.001, 0.001, 0.001, 0.001],
          [0.003, 0.003, 0.005, 0.005, 0.005, 0.004, 0.002, 0.004, 0.004, 0.001, 0.000, 0.000, 0.000, 0.000, 0.001, 0.000],
        

## Investigation - Why is stage 3 zero?

In [12]:
dct['p3'].shape, dct['p3'].sum()

((1, 3, 16, 16), 0.0)

In [13]:
dct['countlayer_x3_'].sum()

5394.3945